In [1]:
import findspark
findspark.init()

import pyspark
import random

In [2]:
sc = pyspark.SparkContext(appName='Exercicio_1_Spark')

2021-12-19 18:11:01,136 WARN util.Utils: Your hostname, bigdatavm-VirtualBox resolves to a loopback address: 127.0.1.1; using 10.0.2.15 instead (on interface enp0s3)
2021-12-19 18:11:01,139 WARN util.Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
2021-12-19 18:11:02,451 WARN util.NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


##### 1. Utilizando o dataset flights.csv, faça operações MapReduce para calcular:
###### a. O tempo total de vôo de cada companhia
###### b. Qual é o destino mais visado
###### c. Quais aeroportos cada companhia passou
###### d. O vôo de maior distância de cada companhia
###### e. Qual é o vôo mais frequente de cada companhia

In [5]:
# A
flights_file = 'file:///home/bigdata-vm/Desktop/BigDataAulasPUC/Datasets/Flights_old/flights.csv'

flights_rdd = sc.textFile(flights_file)

def read_line(line):
    record = line.split(',')
    return (record[1],float(record[9]))

delay_rdd = flights_rdd.map(read_line)
print(delay_rdd.reduceByKey(lambda a,b: a+b).take(10))

[('19930', 2001295.0), ('20409', 3009096.0), ('20366', 4142864.0), ('20437', 799733.0), ('19690', 449242.0), ('20355', 4194811.0), ('21171', 916098.0), ('19805', 6273366.0), ('19790', 7747256.0), ('20436', 689589.0)]


In [6]:
# B
def read_line(line):
    record = line.split(',')
    return (record[4], int(1))

delay_rdd = flights_rdd.map(read_line)
print(delay_rdd.reduceByKey(lambda a,b: a+b).take(10))

[('LAX', 18343), ('ORD', 22615), ('BOS', 9304), ('PBI', 2172), ('DCA', 5831), ('FLL', 5789), ('IAD', 4892), ('PHX', 13433), ('SJU', 2183), ('ONT', 1694)]


In [7]:
# C
def aeroportosOrigem(line):
    record = line.split(',')
    return (record[1],record[3])

def aeroportosDestino(line):
    record = line.split(',')
    return (record[1],record[4])

listaOrigem = flights_rdd.map(aeroportosOrigem).take(90000)
listaDestino = flights_rdd.map(aeroportosDestino).take(90000)

listaOrigem_RDD = sc.parallelize(listaOrigem)
listaDestino_RDD = sc.parallelize(listaDestino)

grouped_elementsDestino = listaOrigem_RDD.union(listaDestino_RDD).distinct().groupByKey().take(10)
for key, values in grouped_elementsDestino:    
    print(key, list(values))

21171 ['AUS', 'DCA', 'PDX', 'DFW', 'SFO', 'LAS', 'JFK', 'SJC', 'EWR', 'PSP', 'FLL', 'BOS', 'PHL', 'SAN', 'LAX', 'SEA', 'ORD', 'IAD', 'MCO']
20436 ['STL', 'SAN', 'CLE', 'MDT', 'MSN', 'SBA', 'PHX', 'FLL', 'OMA', 'TPA', 'BIS', 'MOT', 'PSP', 'MCI', 'TTN', 'GEG', 'MEM', 'OKC', 'LAS', 'SFO', 'MSP', 'BZN', 'FAR', 'BMI', 'SLC', 'CVG', 'ILG', 'LGA', 'MDW', 'DFW', 'BNA', 'FAT', 'JAC', 'DCA', 'PDX', 'MKE', 'DTW', 'AUS', 'FSD', 'SNA', 'ATL', 'LIT', 'CLT', 'MCO', 'MSY', 'IND', 'PHF', 'RDU', 'DEN', 'SEA', 'IAH', 'RSW', 'LAX', 'DSM', 'CID', 'BKG']
19690 ['LAS', 'KOA', 'SFO', 'HNL', 'PDX', 'OAK', 'SAN', 'PPG', 'LAX', 'SEA', 'OGG', 'SJC', 'LIH', 'JFK', 'PHX', 'SMF', 'ITO']
20355 ['SFO', 'LAS', 'MSP', 'PIT', 'KOA', 'STT', 'MCO', 'MSY', 'IND', 'HNL', 'RDU', 'BDL', 'SAT', 'ALB', 'CLT', 'SNA', 'ONT', 'DCA', 'ATL', 'PDX', 'CMH', 'AUS', 'MKE', 'DTW', 'SJU', 'PVD', 'SRQ', 'BTV', 'PHL', 'RNO', 'CLE', 'SAN', 'STL', 'OAK', 'BWI', 'MIA', 'BUF', 'MDT', 'DEN', 'LAX', 'PBI', 'ORD', 'IAH', 'SEA', 'DSM', 'RSW', 'ROC',

In [8]:
# D
def read_line(line):
    record = line.split(',')
    return (record[1],float(record[10]))

delay_rdd = flights_rdd.map(read_line)
print(delay_rdd.reduceByKey(lambda a,b: a+b).take(10))

[('19930', 15133690.0), ('20409', 22096230.0), ('20366', 26726970.0), ('20437', 5615936.0), ('19690', 3317412.0), ('20355', 30257721.0), ('21171', 6985682.0), ('19805', 46572644.0), ('19790', 57091355.0), ('20436', 5019744.0)]


In [9]:
# E
def voos(line):
    record = line.split(',')
    return (record[1],record[3]+'->'+record[4])

lista = flights_rdd.map(voos).collect()
lista_rdd = sc.parallelize(lista)

grouped_elements = lista_rdd.groupByKey().collect()
qtdVoosPorCia = lista_rdd.map(lambda x: (x, 1)).reduceByKey(lambda a,b: a+b).groupByKey().collect()

for key, values in qtdVoosPorCia:
    print(key, list(values))

2021-12-19 18:12:48,182 WARN scheduler.TaskSetManager: Stage 24 contains a task of very large size (2443 KiB). The maximum recommended task size is 1000 KiB.
2021-12-19 18:12:48,952 WARN scheduler.TaskSetManager: Stage 26 contains a task of very large size (2443 KiB). The maximum recommended task size is 1000 KiB.


('19805', 'LAX->MIA') [238]
('19805', 'DFW->FLL') [179]
('19805', 'LAX->IAD') [90]
('19805', 'ORD->PBI') [60]
('19805', 'LAX->SFO') [178]
('19805', 'DEN->ORD') [1]
('19805', 'RDU->MIA') [90]
('19805', 'MSY->ORD') [1]
('19805', 'LAX->BOS') [89]
('19805', 'DFW->SFO') [309]
('19805', 'SFO->DFW') [309]
('19805', 'SFO->ORD') [175]
('19805', 'DFW->DTW') [138]
('19805', 'DTW->DFW') [136]
('19805', 'JFK->SFO') [116]
('19805', 'PHX->MIA') [60]
('19805', 'JFK->DFW') [30]
('19805', 'PHX->DFW') [278]
('19805', 'MIA->BOS') [210]
('19805', 'DFW->EWR') [165]
('19805', 'LAS->LAX') [180]
('19805', 'AUS->JFK') [30]
('19805', 'LGA->ORD') [471]
('19805', 'CMH->DFW') [112]
('19805', 'DFW->CMH') [112]
('19805', 'IND->DFW') [144]
('19805', 'SEA->DFW') [205]
('19805', 'FLL->ORD') [120]
('19805', 'DFW->IAH') [197]
('19805', 'IAH->DFW') [196]
('19805', 'PHL->MIA') [90]
('19805', 'DCA->LAX') [30]
('19805', 'LAX->KOA') [29]
('19805', 'LAX->LIH') [50]
('19805', 'ORD->MIA') [269]
('19805', 'ORD->LAX') [269]
('19805

#### 2 - Utilizando o dataset shakespeare.txt, faça uma operação de MapReduce para construir um índice invertido contendo como chave uma palavra e como valor uma lista de linhas onde ela foi mencionada.

In [3]:
shakespeare_file = 'file:///home/bigdata-vm/Desktop/BigDataAulasPUC/Datasets/shakespeare.txt'
text_rdd = sc.textFile(shakespeare_file)

def read_line(line):
    split = line.split('\t', 1)
    for palavra in split[1].strip().replace('\t', ' ').split():
        yield palavra, int(split[0].split('@')[1])

shakespeare_rdd = text_rdd.flatMap(read_line).groupByKey()
for palavra, linha, in shakespeare_rdd.collect():
    print(palavra, list(linha))


PERSONAE [10, 20, 15, 13, 24, 24, 19, 13, 11, 16, 19, 19, 22, 21, 19, 20, 29, 19, 19, 30, 23, 24, 18, 27, 20, 26, 26, 14, 17, 18, 20, 28, 11, 31, 15, 29, 24]
CLAUDIUS [31, 9319, 11141, 11924, 12169, 12374, 13347, 14869, 46783, 48245, 48765, 49120, 49283, 49560, 50654, 52845, 52955, 53935, 54145, 54379, 54824, 75150, 76257, 76504, 77527, 77847, 82797, 82837, 84001, 88803, 88961, 95686, 95833, 97366, 103001, 104042, 104698, 107425, 118128, 118410, 118718, 119406, 121864, 122485, 122580, 122699, 122764, 123127, 123265, 123400, 123663, 123777, 124126, 124167, 124309, 124480, 130225, 130415, 130812, 131174, 131522, 132631, 133316, 133914, 134287, 134340, 134693, 134843, 135070, 135238, 137465, 138183, 140054, 140090, 140520, 141458, 141886, 142063, 142528, 142799, 142968, 143425, 143748, 144402, 144458, 144566, 145101, 145249, 146048, 147054, 149145, 161549, 162010, 162967, 173518, 173581, 175094, 175257, 175520, 176288, 176587, 176796, 176901, 177093, 177514, 177874, 178576, 178750, 788, 9